In [9]:
import pandas as pd
from sentence_transformers import SentenceTransformer
#import umap.umap_ as umap
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
import nltk
from nltk.corpus import stopwords
from bertopic import BERTopic
import plotly.express as px
from sklearn.cluster import KMeans
import pandas as pd
from sentence_transformers import SentenceTransformer
#import umap.umap_ as umap
import json

In [18]:
import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"


In [2]:
df = pd.read_csv("../Data/raw/df_oilnews.csv")
df

title        Date  \
0      April Price Crash Dragged Saudi Arabia’s Oil R...  2025-06-25   
1      Giant Leviathan Gas Field Offshore Israel Resu...  2025-06-25   
2      China and India Cut Imports of Lower-Quality C...  2025-06-25   
3      Iran-Israel War Prompts China to Reconsider Ru...  2025-06-25   
4        EU Set to Change Subsidy Rules for Energy Costs  2025-06-25   
...                                                  ...         ...   
23415  Australia's Desalinization Plant Workers in In...  2011-06-20   
23416       Chinese Energy Workers in Somalia Threatened  2011-06-19   
23417  Argentina Now Receiving 40 Percent of Chinese ...  2011-06-19   
23418  Chinese Dam and Pipeline Projects Raise Burmes...  2011-06-18   
23419  Russia Remains Committed to Burgas-Alexandroup...  2011-06-18   

                                                 excerpt  
0      Saudi Arabia’s revenues from oil exports crash...  
1      The massive Leviathan gas field offshore Israe...  
2      The world’s biggest and second-biggest coal im...  
3      The war between Israel and Iran has spark worr...  
4      National governments in the EU would soon be a...  
...                                                  ...  
23415  Victoria state’s troubled Wonthaggi desalinati...  
23416  The Ogaden National Liberation Front has warne...  
23417  In Argentina Mandarin Chinese is now the main ...  
23418  Lucrative China-backed hydropower projects are...  
23419  Russian Deputy Energy Minister Anatoli Ianovsk...  

[23420 rows x 3 columns]

In [3]:
from transformers import AutoTokenizer, AutoModel
import torch

model_name = "distilbert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model     = AutoModel.from_pretrained(model_name)

def embed_texts(texts, batch_size=16):
    embeddings = []
    model.eval()
    with torch.no_grad():
        for i in range(0, len(texts), batch_size):
            batch = texts[i : i + batch_size]
            enc = tokenizer(batch, padding=True, truncation=True,
                            return_tensors="pt", max_length=128)
            out = model(**enc)  # out.last_hidden_state shape: [B, L, D]
            mask = enc["attention_mask"].unsqueeze(-1)  # [B, L, 1]
            summed = (out.last_hidden_state * mask).sum(1)      # [B, D]
            counts = mask.sum(1)                               # [B, 1]
            mean_pooled = summed / counts                      # [B, D]
            embeddings.append(mean_pooled.cpu())
    return torch.cat(embeddings).numpy()

# Usage
texts = df['title'].tolist()
embeddings = embed_texts(texts)
df['embeddings'] = embeddings.tolist()



In [4]:
import numpy as np
import umap

X = np.vstack(df['embeddings'].values)  # shape: (n_docs, dim_embed)

# Proiezione 2D
reducer_2d = umap.UMAP(n_components=2, random_state=42)
emb2d = reducer_2d.fit_transform(X)
df['umap2d_1'], df['umap2d_2'] = emb2d[:,0], emb2d[:,1]

# Proiezione 3D
reducer_3d = umap.UMAP(n_components=3, random_state=42)
emb3d = reducer_3d.fit_transform(X)
df['umap3d_1'], df['umap3d_2'], df['umap3d_3'] = emb3d[:,0], emb3d[:,1], emb3d[:,2]


/opt/homebrew/lib/python3.11/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/homebrew/lib/python3.11/site-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
/opt/homebrew/lib/python3.11/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/homebrew/lib/python3.11/site-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by s

In [15]:
df

title        Date  \
0      April Price Crash Dragged Saudi Arabia’s Oil R...  2025-06-25   
1      Giant Leviathan Gas Field Offshore Israel Resu...  2025-06-25   
2      China and India Cut Imports of Lower-Quality C...  2025-06-25   
3      Iran-Israel War Prompts China to Reconsider Ru...  2025-06-25   
4        EU Set to Change Subsidy Rules for Energy Costs  2025-06-25   
...                                                  ...         ...   
23415  Australia's Desalinization Plant Workers in In...  2011-06-20   
23416       Chinese Energy Workers in Somalia Threatened  2011-06-19   
23417  Argentina Now Receiving 40 Percent of Chinese ...  2011-06-19   
23418  Chinese Dam and Pipeline Projects Raise Burmes...  2011-06-18   
23419  Russia Remains Committed to Burgas-Alexandroup...  2011-06-18   

                                                 excerpt  \
0      Saudi Arabia’s revenues from oil exports crash...   
1      The massive Leviathan gas field offshore Israe...   
2      The world’s biggest and second-biggest coal im...   
3      The war between Israel and Iran has spark worr...   
4      National governments in the EU would soon be a...   
...                                                  ...   
23415  Victoria state’s troubled Wonthaggi desalinati...   
23416  The Ogaden National Liberation Front has warne...   
23417  In Argentina Mandarin Chinese is now the main ...   
23418  Lucrative China-backed hydropower projects are...   
23419  Russian Deputy Energy Minister Anatoli Ianovsk...   

                                              embeddings   umap2d_1  umap2d_2  \
0      [-0.17859329283237457, -0.14840400218963623, 0...   8.092489  4.201984   
1      [0.07645712047815323, 0.008211405016481876, -0...  11.803713  4.705826   
2      [-0.09744640439748764, -0.12307503074407578, -...  10.009842  4.151442   
3      [-0.15864795446395874, 0.03611624240875244, -0...   9.039417  6.307949   
4      [0.232235848903656, -0.2532971203327179, 0.231...   8.551908  2.302303   
...                                                  ...        ...       ...   
23415  [0.050046831369400024, -0.0033792087342590094,...  12.909121  4.090429   
23416  [0.2472524642944336, 0.005747473798692226, -0....   7.935728  6.430812   
23417  [-0.23318251967430115, -0.1518239825963974, -0...   8.170956  3.735896   
23418  [0.2948950231075287, 0.1841677874326706, -0.31...  10.131681  5.235997   
23419  [-0.08060380816459656, 0.10930313169956207, 0....  11.547664  6.280421   

        umap3d_1  umap3d_2  umap3d_3  
0       9.806133  4.573699  7.014069  
1      10.414725  5.638460  3.795911  
2       9.673284  4.766704  5.602808  
3       8.095137  5.924802  5.266395  
4       7.946406  2.962389  4.789450  
...          ...       ...       ...  
23415  11.870824  4.807317  4.102218  
23416   9.517726  6.415157  5.788492  
23417   9.729644  4.189168  6.927898  
23418   9.212453  5.679459  5.230610  
23419   9.020863  6.376720  3.355285  

[23420 rows x 9 columns]

In [6]:
df.to_csv("../Data/raw/embeddings_distilbert-base-uncased.csv", index = False)

In [16]:
df = df.rename(columns={
    'umap2d_1': 'embedding_2d_1',
    'umap2d_2': 'embedding_2d_2',
    'umap3d_1': 'embedding_3d_1',
    'umap3d_2': 'embedding_3d_2',
    'umap3d_3': 'embedding_3d_3'
})

In [18]:
df.to_csv("../Data/raw/embeddings_distilbert-base-uncased.csv", index = False)

## Cluster Analysis

In [21]:
df_subset = df.copy()
X = df_subset[['embedding_2d_1', 'embedding_2d_2']].values

k = 20
kmeans = KMeans(n_clusters=k, random_state=42)
clusters = kmeans.fit_predict(X)
df_subset['cluster'] = clusters.astype(str)

big_palette  = px.colors.qualitative.Safe \
             + px.colors.qualitative.Bold \
             + px.colors.qualitative.Light24
colors_for_clusters = big_palette[:k]

fig = px.scatter(
    df_subset,
    x='embedding_2d_1',
    y='embedding_2d_2',
    color='cluster',
    color_discrete_sequence=colors_for_clusters,
    hover_name='title',
    title=f'Cluster analysis con {k} cluster',
    width=900, height=700
)
fig.update_traces(marker=dict(size=8, opacity=0.7))
fig.show()

### Cluster Semantics

In [10]:
nltk.download('stopwords')
stop_words = stopwords.words('english')

def descrivi_cluster(df, n_top_words=20):
    descrizioni = {}
    for cluster_id in sorted(df['cluster'].unique()):
        testi = df[df['cluster'] == cluster_id]['title'].values
        testo_unito = " ".join(testi)
        vectorizer = TfidfVectorizer(stop_words=stop_words, max_features=1000)
        tfidf_matrix = vectorizer.fit_transform([testo_unito])
        feature_names = vectorizer.get_feature_names_out()
        scores = tfidf_matrix.toarray()[0]
        top_indices = scores.argsort()[-n_top_words:][::-1]
        top_words = [feature_names[i] for i in top_indices]
        descrizioni[cluster_id] = ", ".join(top_words)
    return descrizioni

descrizioni = descrivi_cluster(df_subset)
for cluster, parole in descrizioni.items():
    print(f"Cluster {cluster}: {parole}")


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/saraborello/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Cluster 0: gas, gazprom, oil, russia, pipeline, china, rosneft, russian, deal, natural, lng, ukraine, sea, field, supply, europe, south, iran, new, production
Cluster 1: oil, energy, big, new, gas, shell, could, opec, world, lng, aramco, climate, prices, ceo, shale, coal, uk, green, canada, bp
Cluster 10: oil, gas, offshore, lng, new, exxon, first, field, project, production, shell, deal, china, major, bp, sea, refinery, exploration, mexico, drilling
Cluster 11: oil, bpd, 000, million, production, output, barrels, opec, court, gulf, hurricane, mexico, nigeria, billion, crude, iran, libya, pipeline, exports, iraq
Cluster 12: oil, opec, prices, production, demand, gas, price, cuts, year, sees, iea, global, output, forecast, time, growth, first, energy, goldman, eia
Cluster 13: tesla, new, solar, ev, energy, battery, could, car, model, electric, power, musk, china, sales, cars, fuel, wind, production, world, technology
Cluster 14: energy, oil, uk, gas, eu, climate, power, emissions, billi

In [ ]:
descrizioni_cluster = {}

for cluster_id in sorted(df_subset['cluster'].unique()):
    testi_cluster = df_subset[df_subset['cluster'] == cluster_id]['title'].tolist()

    topic_model = BERTopic(language="english")
    topics, probs = topic_model.fit_transform(testi_cluster)
    parole_chiave = topic_model.get_topic(0)

    descrizioni_cluster[cluster_id] = parole_chiave


for cluster_id, parole in descrizioni_cluster.items():
    print(f"Cluster {cluster_id}:")
    print(", ".join([word for word, _ in parole]))
    print("-" * 50)

Cluster 0:
gazprom, gas, to, gazproms, europe, for, in, of, stream, ukraine
--------------------------------------------------
Cluster 1:
shell, merger, ceo, climate, glencore, shareholders, shells, faces, new, to
--------------------------------------------------
Cluster 10:
china, chinese, cnooc, chinas, giant, pipeline, coal, field, oil, gas
--------------------------------------------------
Cluster 11:
court, case, in, against, over, us, shell, for, supreme, uk
--------------------------------------------------
Cluster 12:
goldman, sachs, price, brent, oil, forecast, sees, morgan, to, bank
--------------------------------------------------
Cluster 13:
solar, efficiency, power, cells, cell, panels, energy, can, to, new
--------------------------------------------------
Cluster 14:
canada, oil, alberta, canadian, canadas, sands, industry, pipeline, albertas, jobs
--------------------------------------------------
Cluster 15:
drilling, lease, sale, alaska, gulf, offshore, mexico, bide



| Cluster | Topic                                           | Theme                                                  |
| ------- | ----------------------------------------------- | ------------------------------------------------------ |
| 0       | Russian gas exports to Europe and China         | Geopolitics of energy pipelines                        |
| 1       | Strategic shifts of major oil companies         | Energy companies’ climate and business strategies      |
| 2       | Investment in energy projects                   | Financing of oil, gas and renewable infrastructure     |
| 3       | Impact of sanctions on Iran’s oil exports       | Geopolitical restrictions and crude trade              |
| 4       | Weekly API crude and gasoline inventory reports | US stock fluctuations and price impact                 |
| 5       | Rising LNG demand in Asia                       | Global liquefied natural gas market                    |
| 6       | European winter gas supply crisis               | Energy security and supply vulnerabilities             |
| 7       | OPEC+ production cut decisions                  | Coordination of oil output among member countries      |
| 8       | Quarterly earnings of major energy firms        | Financial performance of oil & gas corporations        |
| 9       | Disruptions to Libyan oil infrastructure        | Geopolitical instability affecting production          |
| 10      | New offshore oil & gas exploration projects     | Deepwater development by international majors          |
| 11      | Global production volumes and outages           | Supply disruptions from natural disasters and outages  |
| 12      | Price and demand forecasts by IEA/EIA/Goldman   | Market outlook and agency/bank analyses                |
| 13      | Innovations in solar panels and EVs             | Advances in renewable energy and battery technology    |
| 14      | UK/EU climate and emissions policy targets      | Regional regulatory frameworks for carbon reduction    |
| 15      | Drilling lease sales in US and Canada           | North American offshore policy and pipeline debates    |
| 16      | Shifts in oil trade flows under sanctions       | Market reconfiguration driven by geopolitical measures |
| 17      | IPOs and asset deals of state oil companies     | Entry of national oil majors into public markets       |
| 18      | Negotiations for new energy pipelines           | International infrastructure agreements                |
| 19      | Record Russian oil & gas exports to Asia        | Expansion of eastern export routes                     |


In [13]:
df_subset

title        Date  \
0      April Price Crash Dragged Saudi Arabia’s Oil R...  2025-06-25   
1      Giant Leviathan Gas Field Offshore Israel Resu...  2025-06-25   
2      China and India Cut Imports of Lower-Quality C...  2025-06-25   
3      Iran-Israel War Prompts China to Reconsider Ru...  2025-06-25   
4        EU Set to Change Subsidy Rules for Energy Costs  2025-06-25   
...                                                  ...         ...   
23415  Australia's Desalinization Plant Workers in In...  2011-06-20   
23416       Chinese Energy Workers in Somalia Threatened  2011-06-19   
23417  Argentina Now Receiving 40 Percent of Chinese ...  2011-06-19   
23418  Chinese Dam and Pipeline Projects Raise Burmes...  2011-06-18   
23419  Russia Remains Committed to Burgas-Alexandroup...  2011-06-18   

                                                 excerpt  \
0      Saudi Arabia’s revenues from oil exports crash...   
1      The massive Leviathan gas field offshore Israe...   
2      The world’s biggest and second-biggest coal im...   
3      The war between Israel and Iran has spark worr...   
4      National governments in the EU would soon be a...   
...                                                  ...   
23415  Victoria state’s troubled Wonthaggi desalinati...   
23416  The Ogaden National Liberation Front has warne...   
23417  In Argentina Mandarin Chinese is now the main ...   
23418  Lucrative China-backed hydropower projects are...   
23419  Russian Deputy Energy Minister Anatoli Ianovsk...   

                                              embeddings   umap2d_1  umap2d_2  \
0      [-0.17859329283237457, -0.14840400218963623, 0...   8.092489  4.201984   
1      [0.07645712047815323, 0.008211405016481876, -0...  11.803713  4.705826   
2      [-0.09744640439748764, -0.12307503074407578, -...  10.009842  4.151442   
3      [-0.15864795446395874, 0.03611624240875244, -0...   9.039417  6.307949   
4      [0.232235848903656, -0.2532971203327179, 0.231...   8.551908  2.302303   
...                                                  ...        ...       ...   
23415  [0.050046831369400024, -0.0033792087342590094,...  12.909121  4.090429   
23416  [0.2472524642944336, 0.005747473798692226, -0....   7.935728  6.430812   
23417  [-0.23318251967430115, -0.1518239825963974, -0...   8.170956  3.735896   
23418  [0.2948950231075287, 0.1841677874326706, -0.31...  10.131681  5.235997   
23419  [-0.08060380816459656, 0.10930313169956207, 0....  11.547664  6.280421   

        umap3d_1  umap3d_2  umap3d_3 cluster  year  
0       9.806133  4.573699  7.014069      19  2025  
1      10.414725  5.638460  3.795911      10  2025  
2       9.673284  4.766704  5.602808      16  2025  
3       8.095137  5.924802  5.266395      18  2025  
4       7.946406  2.962389  4.789450      14  2025  
...          ...       ...       ...     ...   ...  
23415  11.870824  4.807317  4.102218      17  2011  
23416   9.517726  6.415157  5.788492       9  2011  
23417   9.729644  4.189168  6.927898      19  2011  
23418   9.212453  5.679459  5.230610      16  2011  
23419   9.020863  6.376720  3.355285       0  2011  

[23420 rows x 11 columns]

In [14]:
# news over years
df_subset['year'] = pd.to_datetime(df_subset['Date']).dt.year.astype(str)
X = df_subset[['umap2d_1', 'umap2d_2']].values

k = 20
kmeans = KMeans(n_clusters=k, random_state=42)
clusters = kmeans.fit_predict(X)

df_subset['cluster'] = clusters.astype(str)
big_palette = px.colors.qualitative.Safe + px.colors.qualitative.Bold + px.colors.qualitative.Light24
colors_for_clusters = big_palette[:k]

fig = px.scatter(
    df_subset,
    x='umap2d_1',
    y='umap2d_2',
    color='cluster',
    animation_frame='year',
    color_discrete_sequence=colors_for_clusters,
    hover_name='title',
    title=f'Cluster analysis con {k} cluster animata per anno',
    width=900,
    height=700
)

fig.update_traces(marker=dict(size=8, opacity=0.7))
fig.show()


## Feature Creation

In [22]:
df_embeddings = pd.read_csv('../Data/raw/embeddings_distilbert-base-uncased.csv')


In [ ]:
import pandas as pd

df_embeddings['Date'] = pd.to_datetime(df_embeddings['Date'])

df_daily_mean = df_embeddings.groupby(df_embeddings['Date'].dt.date).agg({
    'embedding_2d_1': 'mean',
    'embedding_2d_2': 'mean',
    'embedding_3d_1': 'mean',
    'embedding_3d_2': 'mean',
    'embedding_3d_3': 'mean'
}).reset_index()

df_daily_mean.rename(columns={'Date': 'date'}, inplace=True)
df_daily_mean.rename(columns={
    col: f"{col}_mean" for col in df_daily_mean.columns if col not in ['date']
}, inplace=True)

df_daily_mean.head()


date  embedding_2d_1_mean  embedding_2d_2_mean  embedding_3d_1_mean  \
0  2011-06-18            10.839672             5.758209             9.116658   
1  2011-06-19             8.053342             5.083354             9.623685   
2  2011-06-20            10.168943             4.220067             9.596725   
3  2011-06-21             9.852678             5.405722             9.004225   
4  2011-06-22             9.432877             4.629726             8.864992   

   embedding_3d_2_mean  embedding_3d_3_mean  
0             6.028089             4.292948  
1             5.302163             6.358195  
2             4.739921             5.252258  
3             5.665517             5.114022  
4             4.703284             4.397264

In [ ]:
df_embeddings['Date'] = pd.to_datetime(df_embeddings['Date'])
df_daily_var = df_embeddings.groupby(df_embeddings['Date'].dt.date).agg({
    'embedding_2d_1': 'var',
    'embedding_2d_2': 'var',
    'embedding_3d_1': 'var',
    'embedding_3d_2': 'var',
    'embedding_3d_3': 'var'
}).reset_index()

df_daily_var.rename(columns={'Date': 'date'}, inplace=True)
df_daily_var.rename(columns={
    col: f"{col}_var_daily" for col in df_daily_var.columns if col not in ['date']
}, inplace=True)
df_daily_var['semantic_dispersion_2d'] = df_daily_var[['embedding_2d_1_var_daily', 'embedding_2d_2_var_daily']].mean(axis=1, skipna=True)
df_daily_var['semantic_dispersion_3d'] = df_daily_var[['embedding_3d_1_var_daily', 'embedding_3d_2_var_daily', 'embedding_3d_3_var_daily']].mean(axis=1, skipna=True)
df_daily_var.head()


date  embedding_2d_1_var_daily  embedding_2d_2_var_daily  \
0  2011-06-18                  1.002504                  0.545411   
1  2011-06-19                  0.027666                  3.631286   
2  2011-06-20                  2.460500                  0.904674   
3  2011-06-21                  0.655416                  1.826174   
4  2011-06-22                  3.990852                  2.880831   

   embedding_3d_1_var_daily  embedding_3d_2_var_daily  \
0                  0.018353                  0.243087   
1                  0.022455                  2.477514   
2                  2.237977                  0.326985   
3                  0.401945                  0.592122   
4                  1.016440                  2.608578   

   embedding_3d_3_var_daily  semantic_dispersion_2d  semantic_dispersion_3d  
0                  1.758421                0.773957                0.673287  
1                  0.649123                1.829476                1.049697  
2                  0.504592                1.682587                1.023184  
3                  0.621849                1.240795                0.538639  
4                  1.228204                3.435841                1.617741

In [ ]:
import pandas as pd
import numpy as np
import ast
from sklearn.metrics.pairwise import cosine_similarity

df_embeddings['embedding_array'] = df_embeddings['embeddings'].apply(ast.literal_eval).apply(np.array)

df_daily = df_embeddings.groupby(df_embeddings['Date'].dt.date)['embedding_array'].apply(lambda x: np.mean(np.stack(x), axis=0)).reset_index()
df_daily.rename(columns={'Date': 'date', 'embedding_array': 'embedding_mean'}, inplace=True)

def cosine_sim(v1, v2):
    return cosine_similarity(v1.reshape(1, -1), v2.reshape(1, -1))[0][0]

df_daily['cosine_sim'] = np.nan
for i in range(1, len(df_daily)):
    df_daily.loc[i, 'cosine_sim'] = cosine_sim(df_daily.loc[i, 'embedding_mean'], df_daily.loc[i-1, 'embedding_mean'])


df_daily['drift'] = 1 - df_daily['cosine_sim']

window_size = 3
df_daily['drift_velocity'] = df_daily['drift'].rolling(window=window_size).mean()

df_daily['drift_velocity_diff'] = df_daily['drift_velocity'].diff()
df_daily['drift_acceleration'] = df_daily['drift_velocity_diff'].diff()

print(df_daily[['date', 'cosine_sim', 'drift', 'drift_velocity', 'drift_acceleration']].head(10))


         date  cosine_sim     drift  drift_velocity  drift_acceleration
0  2011-06-18         NaN       NaN             NaN                 NaN
1  2011-06-19    0.881471  0.118529             NaN                 NaN
2  2011-06-20    0.922092  0.077908             NaN                 NaN
3  2011-06-21    0.946231  0.053769        0.083402                 NaN
4  2011-06-22    0.955424  0.044576        0.058751                 NaN
5  2011-06-23    0.956513  0.043487        0.047277            0.013177
6  2011-06-24    0.861742  0.138258        0.075441            0.039637
7  2011-06-25    0.786505  0.213495        0.131747            0.028143
8  2011-06-26    0.829726  0.170274        0.174009           -0.014044
9  2011-06-27    0.926989  0.073011        0.152260           -0.064012


In [30]:
df_daily.dropna(inplace=True)

In [31]:
df_daily['date'] = pd.to_datetime(df_daily['date'])
df_daily_var['date'] = pd.to_datetime(df_daily_var['date'])
df_daily_var = df_daily_var.dropna()
df_daily_mean['date'] = pd.to_datetime(df_daily_mean['date'])

df_merged = pd.merge(df_daily, df_daily_var, on='date', how='inner')
df_merged = pd.merge(df_merged, df_daily_mean, on='date', how='inner')


In [32]:
df_merged.to_csv('embeddings_feature_distilbert-base-uncased.csv',index=False)